In [36]:
import numpy as np
import pandas as pd
from skimage.external.tifffile import *
import glob
import os
from scipy.stats import wasserstein_distance
from skimage import img_as_float

In [37]:
def standardized(img):
    img -= np.mean(img)
    img /= np.std(img)
    return img

def normalized(img):
    img /= np.max(img)
    return img

def standardized_or_normalized(img, bstandardize):
    if bstandardize:
        return standardized(img)
    else:
        return normalized(img)

In [38]:
samples = os.listdir("/data/rgerst_data/Af_labelledSpore_DiDlabelledMHS/input-deconv/")
samples

['ATTC_4µl_3rdReplicate-Experiment-5539',
 'ATTC_DID_5µl_2ndReplicate-Experiment-5453',
 'ATTC_IµL_3rdReplicate-Experiment-5518',
 'ATTC-2µl_3rdReplicate-Experiment-5522',
 'ATTC_DID_3µl_2ndReplicate-Experiment-5437',
 'ATTC_DID_2µl_2ndReplicate-Experiment-5429',
 'ATTC_DID_1µl_2ndReplicate-Experiment-5422',
 'ATTC_1µL_DID_1stReplicate-Experiment-5306',
 'ATTC_1µL_DID_1stReplicate-Experiment-5303',
 'ATTC_DID_6µl_2ndReplicate-Experiment-5460',
 'ATTC_6µl_3rdReplicate-Experiment-5547',
 'ATTC_DID_2µl_2ndReplicate-Experiment-5434',
 'ATTC-2µl_3rdReplicate-Experiment-5525',
 'ATTC_DID_3µl_2ndReplicate-Experiment-5439',
 'ATTC_DID_1µl_2ndReplicate-Experiment-5419',
 'ATTC-5µl_3rdReplicate-Experiment-5541',
 'ATTC_DID_6µl_2ndReplicate-Experiment-5468',
 'ATTC_IµL_3rdReplicate-Experiment-5517',
 'ATTC_6µl_3rdReplicate-Experiment-5550',
 'ATTC_DID_5µl_2ndReplicate-Experiment-5457',
 'ATTC_DID_1µl_2ndReplicate-Experiment-5424',
 'ATTC-2µl_3rdReplicate-Experiment-5523',
 'ATTC_IµL_3rdReplicate-

In [39]:
https://bugs.launchpad.net/ubuntu/+source/openjfx/+bug/1799946https://bugs.launchpad.net/ubuntu/+source/openjfx/+bug/1799946https://bugs.launchpad.net/ubuntu/+source/openjfx/+bug/1799946https://bugs.launchpad.net/ubuntu/+source/openjfx/+bug/1799946https://bugs.launchpad.net/ubuntu/+source/openjfx/+bug/1799946https://bugs.launchpad.net/ubuntu/+source/openjfx/+bug/1799946testcases = ["canny_edges", "dilated", "fft_ifft", "median_filtered", "otsu", "percentile", "wiener2"]
standardize_testcases = [False, True, True, True, False, False, True]

In [40]:
from multiprocessing import Pool

implementations = ["cxx", "java", "python"]
impl_tech = ["misaxx_optMT", "imglib2_nooptMT", "snakemake_optMT"]
df = pd.DataFrame()


for impl, implt in zip(implementations, impl_tech):
    run = "microbench_" + impl + "_" + implt
    
    def run_sample(sample):
        input_img = standardized(img_as_float(imread("/data/rgerst_data/Af_labelledSpore_DiDlabelledMHS/input-deconv/" + sample + "/in/data.tif")))
        row_data = {"implementation": impl, "sample": sample}
        for testcase, enable_standardization in zip(testcases, standardize_testcases):
            if impl == "cxx":
                output_img = standardized_or_normalized(img_as_float(imread(run + "/output-docker/" + sample + "/" + testcase + "/data.tif")), enable_standardization)
                d = wasserstein_distance(output_img.flatten(), input_img.flatten())
                row_data[testcase] = d
            else:
                output_img = standardized_or_normalized(img_as_float(imread(run + "/output/" + sample + "/" + testcase + ".tif")), enable_standardization)
                d = wasserstein_distance(output_img.flatten(), input_img.flatten())
                row_data[testcase] = d
            
        df_row = pd.DataFrame(row_data, index=[0])
        return df_row
    
    with Pool(10) as p:
        for df_row in p.map(run_sample, samples):
            df = df.append(df_row, ignore_index=True)
        
df

implementation                                     sample  canny_edges  \
0              cxx      ATTC_4µl_3rdReplicate-Experiment-5539     0.367649   
1              cxx  ATTC_DID_5µl_2ndReplicate-Experiment-5453     0.399634   
2              cxx      ATTC_IµL_3rdReplicate-Experiment-5518     0.296977   
3              cxx      ATTC-2µl_3rdReplicate-Experiment-5522     0.421572   
4              cxx  ATTC_DID_3µl_2ndReplicate-Experiment-5437     0.238355   
..             ...                                        ...          ...   
388         python  ATTC_2µL_DID_1stReplicate-Experiment-5314     0.341405   
389         python  ATTC_6µL_DID_1stReplicate-Experiment-5375     0.316741   
390         python  ATTC_3µL_DID_1stReplicate-Experiment-5323     0.341362   
391         python      ATTC-3µl_3rdReplicate-Experiment-5526     0.296227   
392         python  ATTC_1µL_DID_1stReplicate-Experiment-5304     0.348276   

      dilated      fft_ifft  median_filtered      otsu  percentile   wiener2  
0    0.370990  3.617451e-03         0.064981  0.348646    0.609635  0.168653  
1    0.394504  2.120034e-03         0.050663  0.380957    0.611302  0.604827  
2    0.238204  1.585960e-03         0.053653  0.289232    0.543300  0.576406  
3    0.443632  2.022622e-03         0.065653  0.398556    0.627004  0.518826  
4    0.255383  1.182519e-03         0.102555  0.232420    0.521741  0.674800  
..        ...           ...              ...       ...         ...       ...  
388  0.388412  1.837990e-07         0.045435  0.325249    0.596977  0.736231  
389  0.315257  1.571610e-07         0.194719  0.301564    0.575200  0.692945  
390  0.413895  5.759171e-08         0.040675  0.325043    0.599021  0.731936  
391  0.270041  3.557055e-08         0.053097  0.287228    0.550937  0.599465  
392  0.353006  1.090643e-07         0.076803  0.332029    0.594120  0.731768  

[393 rows x 9 columns]

In [41]:
df.to_csv("analysis//microbench/distances.csv", index=False)